In [1]:
import re
import requests
import pandas

In [2]:
url1 = "http://finance.jxufe.edu.cn/news-list-jiaoshou-1.html" 
url2 = "http://finance.jxufe.edu.cn/news-list-jiaoshou-2.html"

爬取总页面所有教授网址

In [3]:
def get_html(url):
    url_text = requests.get(url).text
    html_sum = re.findall(r'<div class="pic"> <a href="(.*?)"><img style="width:130px;height:160px;" src=".*?"></a></div>',url_text,re.S)
    return html_sum

爬取基本信息

In [4]:
def get_basis_infor(html):    
    html_text = requests.get(html).text
    d1 = {}
    basis_infor = re.findall(r'<div class="ne_main_R">(.*?)自我简介', html_text,re.S)
    list_infor = re.findall(r'.*?<p>.*?<strong.*?>(.*?)</p>', basis_infor[0],re.S)
    for each in list_infor:
        x = each.replace("&nbsp;","").replace("：","").replace(":","").split("</strong>")
        x1_clear = re.sub(r'<(.*?)>','',x[0]).replace('\u3000','').replace(' ','').strip()
        x2_clear = re.sub(r'<(.*?)>','',x[1]).replace('\u3000','').replace(' ','').strip()
        d1[x1_clear] = x2_clear
    return d1

爬取自我简介

In [5]:
def get_self_intro(html):        
    html_text = requests.get(html).text
    self_intro = re.findall(r'自我简介(.*?)科研成果', html_text,re.S)
    self_intro_text = re.sub(r'</p>','\n',self_intro[0])
    self_intro_text_clear = re.sub(r'<(.*?)>','', self_intro_text).replace("&nbsp;","").replace("\n"," ").strip()
    return self_intro_text_clear

爬取科研成果

In [6]:
def get_sci_res(html):
    html_text = requests.get(html).text
    sci_res = re.findall(r'自我简介.*?科研成果(.*?)版权所有', html_text,re.S)
    sci_res_text = re.sub(r'</p>','\n',sci_res[0])
    sci_res_text_clear = re.sub(r'<(.*?)>','', sci_res_text).replace("&nbsp;","").replace("\n"," ").strip("：").strip()
    return sci_res_text_clear

检索不符合模板的教授,并将其序列号放入列表

In [7]:
z1 = get_html(url1)
z2 = get_html(url2)
def check_html(z):
    l = []
    for n in range(len(z1)):
        try:
            get_basis_infor(z1[n])
            get_self_intro(z1[n])
            get_sci_res(z1[n])
        except:
            l.append(n)
    return l

## 在程序运行中，只有第一页的桂荷发教授不符合该模板

打印所有教授信息(字典)，并整合进一个列表；其中，基本信息中我们只读取以下基本项，避免其他干扰项

In [8]:
pro_sum = []
list1 = ["姓名","性别","出生年月","政治面貌","毕业院校","毕业专业","职务","职称","邮箱","电子邮箱","联系方式"]

第一页的教授信息

In [9]:
for each_z1_1 in range(len(z1)):
    for each_z1_2 in check_html(z1):
        if each_z1_1 != each_z1_2:
            teacher = {}
            for key,value in get_basis_infor(z1[each_z1_1]).items():
                if key in list1:
                    teacher[key] = value
                else:
                    continue
            teacher["自我简介"] = get_self_intro(z1[each_z1_1])   
            teacher["科研成果"] = get_sci_res(z1[each_z1_1])
            pro_sum.append(teacher)
            del teacher
        else:
            continue

第二页的教授信息

In [10]:

for each_z2_1 in range(len(z2)):
    for each_z2_2 in check_html(z2):
        if each_z2_1 != each_z2_2:
            teacher = {}
            for key,value in get_basis_infor(z2[each_z2_1]).items():
                teacher[key] = value
            teacher["自我简介"] = get_self_intro(z2[each_z2_1])   
            teacher["科研成果"] = get_sci_res(z2[each_z2_1])
            pro_sum.append(teacher)
            del teacher
        else:
            continue

pro_sum即为整合所有教授信息的列表（每个教授处于不同的字典中）

In [11]:
pro_sum

[{'姓名': '曹邓',
  '性别': '女',
  '出生年月': '',
  '政治面貌': '中共党员',
  '毕业院校': '江西财经大学',
  '毕业专业': '管理学',
  '职务': '系副主任',
  '职称': '教授',
  '邮箱': 'laotoutou@aliyun.com',
  '自我简介': '一、开设课程：保险学原理、财产保险、保险中介管理、保险实务研究、商业保险理论与研究、财产保险理论与创新 二、获得奖励：1996年获江西财经大学优秀工作者称号；2001年获江西财经大学优秀班主任称号；2003年、2010年获江西财经大学先进工作 者称号；2003年被评为江西财经大学金融学院优秀教师二等奖，2004年获江西省高校优秀班主任称号。2006年获江西省师德师风标兵称号 三、社会兼职：中国保险学会会员、江西保险学会会员',
  '科研成果': '一、论文 1.“WTO:中国民族保险业的机遇与挑战”，独著，《理论导报》2000年第9期。 2.“保险费率的构成及其厘定”，独著，《江西财经大学学报》2000年第1期。 3.“如何评价高新技术企业价值”，独著，《澳港信息日报》（中国投资）2002年5月15日。 4.“加强财政监管，促进社会保障税费改革”，独著，《时策聚焦》2002年1月。 5.“开征社会保障税，摆脱养老保险基金筹资困境”，独著，《探索与创新》2002年8月”。 6.“经济全球化背景下的就业环境、就业结构与就业保障”，独著，《社会保障问题研究》2003年9月。 7.“我国保险资金运用与债券市场发展问题探讨”，独著，《未来与发展》2004年第4期。 8.“论我国保险信用体系的建设”，独著，《未来与发展》2004年第6期。 9.“我国保险资金运用与债券市场发展问题探讨”，独著，《未来与发展》2004年第4期。 10.“我国存款保险制度运行模式的构想”，独著，《价格月刊》2004年第10期。 11.“保险诚信问题分析与保险诚信体系建设”，独著，《金融与经济》2005年第11期。 12.“可持续发展思想的演变与诠释》‘独著，《当代财经》2005年第11期。 13.“《论我国农户小额信贷需求的层次性》，第一作者，《价格月刊》2007第八期。 14.“对我国财产保险创新及创新路径之若干问题的思考”独著，《价格月刊》2008年第12期。 

将列表转换成表格

In [12]:
dict1 = pro_sum[0]
dict2 = {key:value for key,value in dict1.items() if value not in key}
list1 = list(dict1.keys())
list2 = []
date = {}
for i in range(len(dict1)):
    list2.append([])    
for each1 in pro_sum:
    for n in range(len(dict1)):
        list2[n].append(list(each1.values())[n])    
for m in range(len(dict1)):
    date[list1[m]] = list2[m]
    
dateframe = pandas.DataFrame(date)

In [13]:
dateframe

姓名 性别     出生年月  政治面貌         毕业院校             毕业专业          职务  \
0    曹邓  女           中共党员       江西财经大学              管理学        系副主任   
1   陈春霞  女             群众       江西财经大学              金融学               
2   陈家洪  男           中共党员       江西财经大学     经济统计（证券研究方向）               
3   黄飞鸣  男           民革党员         厦门大学              金融学               
4   胡援成  男           中共党员         厦门大学              金融学        中心主任   
5   吕江林  男           中共党员       中南财经大学              经济学  应用金融研究中心主任   
6   刘兴华  男           中共党员         厦门大学             世界经济         副院长   
7   凌爱凡  男           中共党员       西安交通大学             计算数学               
8   彭玉镏  男  1973年3月  中共党员       上海财经大学              金融学               
9   蒋崇辉  男   1980.9  中共党员       电子科技大学  管理科学与工程（金融工程方向）          教授   
10  孙爱琳  女           中共党员         浙江大学            政治经济学               
11   王辉              中共党员       江西财经大学              财政学               
12   汪洋  男           中共党员       上海财经大学              金融学               
13   肖峻  男             民进  同济大学经济与管理学院            管理学博士         副院长   
14   杨荣  女           中共党员       江西财经大学              金融学               
15   严武  男             党员       江西财经大学              经济学               

               职称                     邮箱  \
0              教授   laotoutou@aliyun.com   
1           教授/硕导        new9360@163.com   
2           教授/硕导         jxmcjh@126.com   
3        教授/硕士生导师       172348582@qq.com   
4           教授/博导          hu-yc@163.com   
5           教授/博导        ljl5983@126.com   
6           教授/博导        lxh7572@126.com   
7           教授/博导       aiffling@163.com   
8           教授/博导                          
9   金融工程系主任，博士生导师        jch0920@163.com   
10          教授、硕导        sal6660@126.com   
11          教授/硕导         wh6660@126.com   
12          教授/博导  wangyang@jxufe.edu.cn   
13          教授/博导    xiao_jun913@163.com   
14          教授、硕导   yonghongyang@163.com   
15             教授       923108620@qq.com   

                                                 自我简介  \
0   一、开设课程：保险学原理、财产保险、保险中介管理、保险实务研究、商业保险理论与研究、财产保险...   
1   开设课程 本科生主讲的主要课程有：《货币银行学》、《国际金融》《金融企业会计》、《投资项目评...   
2       一、开设课程：证券投资学、证券投资基金、投资管理、创业投资管理、私募股权投资、证券投资分析   
3   黄飞鸣，河南永城人，经济学博士，现系江西财经大学金融学院教授、博士生导师，江西省高校中青年骨...   
4   一、开设课程：本科：国际金融管理；硕士研究生：公司金融；博士研究生：公司金融理论与政策，外文...   
5   一、开设课程本科生课程:货币银行学、国际金融、证券投资学、商业银行经营管理学、金融工程硕士生...   
6   一、开设课程 系统讲授《国际金融》、《国际货币与金融经济学》、《货币银行学》、《中央银行学》...   
7   一、基本情况    凌爱凡：江西财经大学金融学首席教授，博士生导师，江西财经大学金融科技与监...   
8   开设课程 宏观审慎监管理论与政策（博士课程）、金融监管（硕士课程）、国际金融、金融机构风险管...   
9   1.教育和培训经历  2014.5-2015.4：加拿大/温莎大学Odette商学院（访问学...   
10  一、开设课程 本科生：货币银行学、财政学、预算会计、保险学、保险会计、社会保障学等。 研究生...   
11  一、开设课程 本科生：“保险学”；“人身保险”；“责任保险”；“保险经营管理”；“保险营销学...   
12  一、开设课程：本科：《国际金融》，《国际货币与金融经济学》，《中央银行学》；硕士研究生：《国...   
13  一、从业经历与学术简历  同济大学博士、民进财大副主委，现任金融管理国际研究院副院长、教授、...   
14    一、开设课程：货币银行学、商业银行学、 二、获得奖励：略 三、社会兼职：江西省货币学会常务理事   
15  简介：    严武，现任江西财经大学金融学教授（国家二级）、博士生导师，江西财经大学金融研究...   

                                                 科研成果  
0   一、论文 1.“WTO:中国民族保险业的机遇与挑战”，独著，《理论导报》2000年第9期。 ...  
1   一、论文 1、《我国国债与企业债券的比较》，独著，《江西财经大学学报》2006年第9月期（人...  
2   一、论文1. “从股票市场角度看收入分配不公问题”，独著，《华东经济管理》2011年第8期。...  
3   （一）学术论文（发表学术论文60余篇，代表性论文有：  1.Huang Feiming.Em...  
4   一、论文1、“地价模型初探”，独著，数量经济与技术经济研究 1990年第6期。2、“商业银行...  
5   主要科研成果一、论文1、《具有联合椭圆不确定集与概率约束的鲁棒投资组合选择》，《控制与决策》...  
6   一、论文 1.“日本银行对日元汇率的干预：基于动态博弈的分析”，第一作者，《现代日本经济》2...  
7   英文期刊论文  [15] AifanLing（凌爱凡），Jie Sun，Meihua Wan...  
8   一、论文 1.“人民币外汇市场压力及其影响因素研究——基于LT-TVP-VAR模型的实证分析...  
9   1.研究兴趣 研究兴趣主要表现在资产组合选择和资产定价方面。  2.研究成果 2.1 公开发...  
10  一、论文 1.“完善我国国家公务员养老保险制度的思考”，独著，《江西财经大学学报》2001年...  
11  一、论文 1.“加快建立有中国特色的社会保障法律体系”，独著，《财经论丛》2000年第3期。...  
12  发表的主要论文：1. 《跨境贸易以人民币结算：路径选择与风险》，《国际经济评论》，独著，20...  
13  一、部分权威论文  1.关于中国股市中风格投资与风格动量的研究，《经济科学》，2006年第6...  
14  一、论文 2000年以来论文 1、影响我国企业集团形成与健康发展原因剖析 《国民经济运行与调...  
15  主要成果：  （一）论文论著 1. 中国股市周期的划分与实证分析：1991-2004（第一作...